In [2]:
from bs4 import BeautifulSoup
import requests

In [25]:
# def getLinkMenu(selector, index):
#     return html.select(selector)[index].select('a')[0].get('href')

# href = getLinkMenu('.list-group-item', 1)

# url = f'https://www.biblio-globus.ru{href}'

# r = requests.get(url)

# htmlCategory = BeautifulSoup(r.content, 'html.parser')

# btnAll = htmlCategory.select('.btn-product-preview')[0].get('href')
# print(btnAll)

parts = [
    {'url': 'https://www.biblio-globus.ru/catalog/category?id=241', 'page': 107},
    {'url': 'https://www.biblio-globus.ru/catalog/category?id=242', 'page': 7},
    {'url': 'https://www.biblio-globus.ru/catalog/category?id=248', 'page': 7},
    {'url': 'https://www.biblio-globus.ru/catalog/category?id=6183', 'page': 4},
    {'url': 'https://www.biblio-globus.ru/catalog/category?id=262', 'page': 19},
    {'url': 'https://www.biblio-globus.ru/catalog/category?id=263', 'page': 34},
    {'url': 'https://www.biblio-globus.ru/catalog/category?id=6173', 'page': 53}
]

parts_notpage = [
    'https://www.biblio-globus.ru/catalog/category?id=6174'
]

# 1 - запускаем цикл по parts, где на каждой итерации выполняем requests.get + BeautifulSoup (html) для получения html кода страницы
# 2 - находим кнопку пагинации с двумя стрелками и получаем из нее максимальние количество страниц
# 3 - находим ссылку для перехода на продукт и получаем html страницы продукта
# 4 - находим и сохраняем в csv необходимые атрибуты ()



In [8]:
def saves(value, filename):
    with open(filename, 'a') as out_file:  # with ... as - это более удобная конструкция
        out_file.write(str(' '.join(value)))
        
        
def combinePath(path, page):
    return f'{path}&page={page}'

def getProductIds(path):
    r = requests.get(path)
    html = BeautifulSoup(r.content, 'html.parser')
    books = html.select('.product')
    res = []

    for book in books:
        href = book.select('a')[0].get('href')
        res.append(href)

    return res


# ids = getProductIds(combinePath('https://www.biblio-globus.ru/catalog/category?id=241', 1))

def getPageIds(url, pages):
    for page in range(1, pages):
        path = combinePath(url, page)
        ids_books = getProductIds(path)
        saves(ids_books, '2.txt')
    
    
getPageIds('https://www.biblio-globus.ru/catalog/category?id=204', 199)
    

In [9]:
import csv
import pandas as pd
import os

In [10]:
def readProducts():
    with open('2.txt', 'r') as f:
        my_lines = f.readlines()
        return my_lines[0].split(' ')
    

products = readProducts()

#product/10628872
def getBookData(path):
    data = {
        "page_url": f'https://www.biblio-globus.ru/{path}',
        "image_url": "None",
        "author": "None",
        "title": "None",
        "annotation": "None"
    }
    try:
        r = requests.get(f'https://www.biblio-globus.ru/{path}')
        html = BeautifulSoup(r.content, 'html.parser')

        product = html.select('#productMain')[0]
        url_img = product.select('img')[0].get('src')
        author = product.select('.goToDescription')[0].select('a')[0].text
        title = product.select('.item-desc')[0].select('h1')[0].text

        annotation = product.select('.collapse')[0].contents[0].text

        page_url = f'https://www.biblio-globus.ru/{path}'

        data['page_url'] = page_url

        data['image_url'] = url_img

        data['title'] = title.lstrip().rstrip()

        data['annotation'] = annotation.lstrip().rstrip()

        data['author'] = author.lstrip().rstrip()

        return data
    except:
        return None

    
# Проверяем, существует ли файл. Если нет, создаем и записываем заголовки
file_exists = os.path.isfile('csv_file.csv')
if not file_exists:
    with open('csv_file.csv', mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(["page_url", "image_url", "author", "title", "annotation"])


def parser():
    for item in products:
        data = getBookData(item)

        print(data)
        
        if data != None:
            with open('csv_file.csv', mode='a', newline='', encoding='utf-8') as file:
                writer = csv.writer(file)
                writer.writerow([data["page_url"], data["image_url"], data["author"], data["title"], data["annotation"]])


parser()


{'page_url': 'https://www.biblio-globus.ru//product/10988213', 'image_url': 'https://static1.bgshop.ru/imagehandler.ashx?filename=10988213.jpg&width=550', 'author': 'Маринина А.', 'title': 'Генрих Четвертый и Генрих Пятый глазами Шекспира', 'annotation': 'Он мечтал изменить историю победами и завоеваниями, а изменил ее — своей смертью.  Юный принц Генрих ведет беспутный образ жизни вместе с весельчаком Фальстафом и другими приятелями. Но вот его отец, Генрих Четвертый, умирает. И новый король, Генрих Пятый, неожиданно для многих крепко хватается за власть.\n\tОн верит: Бог и Англия ждут от него завоевания Франции, а заодно — руки и сердца французской принцессы Екатерины, дочери Безумного Короля... «Если счесть пороком — желать без меры славы, то, клянусь, Я самый страшный грешник!»Александра Маринина предлагает увлекательное историческое расследование, почему правители торжествуют на полях сражений, но проигрывают собственным демонам. Главным свидетелем и экспертом выступает гениальный

In [11]:
import pandas as pd

data = pd.read_csv("csv_file.csv")

data

page_url  \
0     https://www.biblio-globus.ru//product/10988213   
1     https://www.biblio-globus.ru//product/10997386   
2     https://www.biblio-globus.ru//product/10712660   
3     https://www.biblio-globus.ru//product/10921063   
4     https://www.biblio-globus.ru//product/10994568   
...                                              ...   
1676  https://www.biblio-globus.ru//product/10639840   
1677  https://www.biblio-globus.ru//product/10619460   
1678  https://www.biblio-globus.ru//product/10619456   
1679  https://www.biblio-globus.ru//product/10610217   
1680  https://www.biblio-globus.ru//product/10602713   

                                              image_url  \
0     https://static1.bgshop.ru/imagehandler.ashx?fi...   
1     https://static1.bgshop.ru/imagehandler.ashx?fi...   
2     https://static1.bgshop.ru/imagehandler.ashx?fi...   
3     https://static1.bgshop.ru/imagehandler.ashx?fi...   
4     https://static1.bgshop.ru/imagehandler.ashx?fi...   
...                                                 ...   
1676  https://static1.bgshop.ru/imagehandler.ashx?fi...   
1677  https://static1.bgshop.ru/imagehandler.ashx?fi...   
1678  https://static1.bgshop.ru/imagehandler.ashx?fi...   
1679  https://static1.bgshop.ru/imagehandler.ashx?fi...   
1680  https://static1.bgshop.ru/imagehandler.ashx?fi...   

                          author  \
0                    Маринина А.   
1                Мартен-Люган А.   
2                    Корнуэлл Б.   
3                    Шейнин Л.Р.   
4                       Брукс С.   
...                          ...   
1676  Алексей Николаевич Толстой   
1677               Алексеев С.П.   
1678  Анатолий Васильевич Митяев   
1679          Александрова З. Н.   
1680    Андрей Алексеевич Усачев   

                                                  title  \
0      Генрих Четвертый и Генрих Пятый глазами Шекспира   
1                       Последнее приключение странника   
2                                           Война волка   
3                          Военная тайна. Мирное время…   
4     Территория чудовищ. Путеводитель для осторожны...   
...                                                 ...   
1676           Приключения Буратино, или Золотой ключик   
1677                                  Матросское сердце   
1678                                           Землянка   
1679                                          Мой мишка   
1680                          Азбука умной собачки Сони   

                                             annotation  
0     Он мечтал изменить историю победами и завоеван...  
1     Профессиональный дайвер Гари и владелец бара И...  
2     Доблестный полководец Утред отвоевал свое родо...  
3     Апрель 1945 года. Американская разведка решает...  
4     Преодолеть гигантское одичалое пространство ме...  
...                                                 ...  
1676  Книгу «Приключения Буратино, или Золотой ключи...  
1677  (6+) Автор - известный детский писатель, участ...  
1678  Анатолий Васильевич Митяев (1924—2008) — автор...  
1679  Наверное, у каждого ребёнка в детстве был свой...  
1680  Всеми любимая умная собачка Соня давно выучила...  

[1681 rows x 5 columns]